In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import sys

ROOT_DIR = '../'
sys.path.insert(1, '../production_code/')
from constants import *

2000_to_20005 is a whole seperate dataset, same columns, might ignore it for now, filter by dates

## from 


| csv name | from documentation | from experimentation |
| ---| --- | --- |
| ACCIDENT_CHAINAGE |  | more specific location data |
| ACCIDENT_EVENT | accident_event (sequence of events e.g. left road, rollover, caught fire) | + location of impact on car |
| ACCIDENT_LOCATION |  | geographical location (street names no GPS) |
| ACCIDENT | accident (basic accident details, time, severity, location) | Main dataframe, general info |
| ATMOSPHERIC_COND | atmospheric_cond (rain, winds etc) | |
| NODE_ID_COMPLEX_INT_ID |  |  for breaking down complex intersections |
| NODE | Node Table with Lat/Long references | Lat/long and LGA areas |
| PERSON | person (person based details, age, sex etc) | |
| ROAD_SURFACE_COND | road_surface_cond (whether road was wet, dry, icy etc)  | |
| Statistic Checks |  | some general stats |
| SUBDCA | sub_dca (detailed codes describing accident) | eg vehicle entering or leaving intersection etc.. |
| VEHICLE | vehicle (vehicle based data, vehicle type, make etc) | |

## from documentation

- accident_node (master location table - NB subset of accident table) 


## features of interest

| Feature | description | dataset
| ---- | ---- |
| ACCIDENT_NO | individual accident id, one id for each accident | all |
| NODE_ID | locational node where the incident occured, 0 is unable to locate | NODE |
| ACCIDENTDATE | date | ACCIDENT |
| ACCIDENTTIME | time | ACCIDENT |
| ATMOSPH_COND | int 0-9, General weather data, check crash stats apendecies | ATMOSPHERIC_COND |
| ATMOSPH_COND_SEQ | int 0-4, not sure, ignoring | ATMOSPHERIC_COND |
| LIGHT_CONDITION | | ACCIDENT
| ACCIDENT_TYPE | type of colision, hit animal, ped etc... | ACCIDENT
| SEVERITY | non injury (0) - fatal (died in 30 days) (1) | ACCIDENT
| ROAD_GEOMETRY | Cross intersection - not at an intersection | ACCIDENT
| POLICE_ATTEND | whether police attended or not | ACCIDENT
| VEHICLE_ID | information of a vehicle | ACCIDENT_EVENT  
| ATMOSPH_COND_SEQ | not sure, if the weather changes maybe? | ATMOSPHERIC_COND
| COMPLEX_INT_NO | for breaking down complex intersections  into sub chunks | NODE_ID_COMPLEX_INT_ID
| LGA_NAME | local goverment area | NODE
| REGION_NAME | more granial area if needed | NODE
| TAKEN_HOSPITAL | is a person was taken to hospital | PERSON
| ROAD_USER_TYPE | where the person was in realtion to the accident | PERSON
| SURFACE_COND | road condition | ROAD_SURFACE_COND


## ideas for the project

1. Comparing intersection crash data year on year to see which intersections improve
2. Predict number of incidents using
    1. features
        1.  weather data
        2.  SURFACE_COND
            1.  too related to weather data?
        3.  location data
            1.  node, LGA, Region?
        4. night or day
           1. might be too related to time?
        5. Datetime
           1. Time of day (1, 2, 4, or 6 hour bins)
           2. Day of week (or just weekday vs weekend etc...)
           3. month of year (maybe creates overfitting, too granular?)

    2. labels, what 
        1. count of Police attended
        2. Mean severity (or own severity metric)
           1. no_persons
           2. no_vehicles
           3. other NO_PERSON metrics
           4. number of people taken to hospitals
        3. straight count of incidents
    
    3.  to filter on
        1. accident_type: remove non colisions?
        2. SEVERITY: remove non injury?
        3. POLICE_ATTEND (not known category)
        4. unique ACCIDENT_NO
        5. check surface condition link to weather data


In [21]:




# compare columns
# list(set(pd.read_csv(ROOT_DIR + DATA_RAW_DIR + 'ACCIDENT\ACCIDENT_EVENT.csv').columns) - set(pd.read_csv(ROOT_DIR + DATA_RAW_DIR + 'ACCIDENT\ACCIDENT.csv').columns))


# comparing acciendent.csv from general to 2000_to_20005

len(list(set(pd.read_csv(ROOT_DIR + DATA_RAW_DIR + '2000_to_2005_ACCIDENT\ACCIDENT.csv')['ACCIDENT_NO']) - set(pd.read_csv(ROOT_DIR + DATA_RAW_DIR + 'ACCIDENT\ACCIDENT.csv')['ACCIDENT_NO'])))

C:\Users\andre\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.9_qbz5n2kfra8p0\LocalCache\local-packages\Python39\site-packages\IPython\core\interactiveshell.py:3441: DtypeWarning: Columns (0) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)
C:\Users\andre\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.9_qbz5n2kfra8p0\LocalCache\local-packages\Python39\site-packages\IPython\core\interactiveshell.py:3441: DtypeWarning: Columns (10,13) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


103061

In [59]:
pd.read_csv(ROOT_DIR + DATA_RAW_DIR + "ACCIDENT/ACCIDENT_CHAINAGE.csv").iloc[0]
# pd.read_csv(ROOT_DIR + DATA_RAW_DIR + "ACCIDENT/ATMOSPHERIC_COND.csv").groupby('ATMOSPH_COND')['ATMOSPH_COND_SEQ'].unique()
# pd.read_csv(ROOT_DIR + DATA_RAW_DIR + "ACCIDENT/PERSON.csv").groupby('TAKEN_HOSPITAL').count()['ACCIDENT_NO']

Node Id                    4
Route No            109454.0
Chainage Seq             1.0
Route Link No    109454801.0
Chainage               908.0
Name: 0, dtype: object

In [34]:
pd.read_csv(ROOT_DIR + DATA_RAW_DIR + "ACCIDENT/ATMOSPHERIC_COND.csv")['ATMOSPH_COND_SEQ'].unique()

array([1, 0, 2, 3, 4], dtype=int64)

In [26]:
len(pd.read_csv(ROOT_DIR + DATA_RAW_DIR + "ACCIDENT/NODE.csv")['NODE_ID'].unique())
# len(pd.read_csv(ROOT_DIR + DATA_RAW_DIR + "ACCIDENT/ACCIDENT_LOCATION.csv")['NODE_ID'].unique())
pd.read_csv(ROOT_DIR + DATA_RAW_DIR + "ACCIDENT/NODE.csv")

ACCIDENT_NO  NODE_ID NODE_TYPE  VICGRID94_X  VICGRID94_Y    LGA_NAME  \
0       T20060002689       22         I  2495701.925  2411599.135   MELBOURNE   
1       T20060010827       22         I  2495701.925  2411599.135   MELBOURNE   
2       T20060017279       22         I  2495701.925  2411599.135   MELBOURNE   
3       T20060041762       22         I  2495701.925  2411599.135   MELBOURNE   
4       T20060047478       22         I  2495701.925  2411599.135   MELBOURNE   
...              ...      ...       ...          ...          ...         ...   
221792  T20090046106   229103         N  2499211.462  2428380.388  WHITTLESEA   
221793  T20090046106   229103         N  2499211.462  2428380.388  WHITTLESEA   
221794  T20090047746   229114         N  2508240.178  2412119.954  BOROONDARA   
221795  T20090044445   229087         N  2653269.886  2599283.209      INDIGO   
221796  T20090046194   229105         N  2592208.478  2362963.486     BAW BAW   

       LGA_NAME_ALL                     REGION_NAME  DEG_URBAN_NAME  \
0         MELBOURNE  METROPOLITAN NORTH WEST REGION      MELB_URBAN   
1         MELBOURNE  METROPOLITAN NORTH WEST REGION      MELB_URBAN   
2         MELBOURNE  METROPOLITAN NORTH WEST REGION      MELB_URBAN   
3         MELBOURNE  METROPOLITAN NORTH WEST REGION      MELB_URBAN   
4         MELBOURNE  METROPOLITAN NORTH WEST REGION      MELB_URBAN   
...             ...                             ...             ...   
221792   WHITTLESEA  METROPOLITAN NORTH WEST REGION      MELB_URBAN   
221793   WHITTLESEA  METROPOLITAN NORTH WEST REGION  RURAL_VICTORIA   
221794   BOROONDARA  METROPOLITAN SOUTH EAST REGION      MELB_URBAN   
221795       INDIGO            NORTH EASTERN REGION  RURAL_VICTORIA   
221796      BAW BAW                  EASTERN REGION  RURAL_VICTORIA   

              Lat        Long  POSTCODE_NO  
0      -37.796596  144.951197         3051  
1      -37.796596  144.951197         3051  
2      -37.796596  144.951197         3051  
3      -37.796596  144.951197         3051  
4      -37.796596  144.951197         3051  
...           ...         ...          ...  
221792 -37.645401  144.991064         3076  
221793 -37.645401  144.991064         3076  
221794 -37.791877  145.093559         3104  
221795 -36.092861  146.702041         3688  
221796 -38.230181  146.053062         3823  

[221797 rows x 12 columns]

In [9]:
local = pd.read_csv(ROOT_DIR + DATA_RAW_DIR + "2000_to_2005_ACCIDENT\\NODE.csv")
fig = px.scatter_mapbox(local, lat="Lat", lon="Long", hover_name="ACCIDENT_NO") 

fig.update_geos(resolution=50)
fig.update_layout( # Update the layout
    geo = dict( # Specify mapbox parameters
        center = dict( # Set the centre point
            lat = -37.8136, # Latitude of Melbourne
            lon = 144.9631 # Longitude of Melbourne
        )
    )
)
fig.show() # Show the plot